In [4]:
from langchain_core.prompts import PromptTemplate
from langchain.chains import RetrievalQA
from langchain_community.embeddings import HuggingFaceEmbeddings
from langchain_community.document_loaders import PyPDFLoader ,DirectoryLoader
from langchain_text_splitters import RecursiveCharacterTextSplitter
from langchain_text_splitters import TokenTextSplitter
import os
from dotenv import load_dotenv

# Loading API keys
load_dotenv()

True

loading the data


In [22]:
# extarct the data from PDF
def load_pdf(data_dir):
    loader =DirectoryLoader(data_dir,
                            glob = "*.pdf",
                            loader_cls =PyPDFLoader)
    documents = loader.load()
    return documents
extracted_data = load_pdf(r"C:\github\openai\athina-ai\data")
# creating textn chunks 
def text_split(extracted_data):
    text_splitter = RecursiveCharacterTextSplitter(
        chunk_size = 10000,
        chunk_overlap = 0
    )
    text_chunks = text_splitter.split_documents(extracted_data)
    return text_chunks
docs = text_split(extracted_data)

In [12]:
len(docs)

44

genrating syntetic data for evaluation

In [29]:
prompt_template = """
Your task is to write a factoid question and an answer given a context.
Your factoid question should be answerable with a specific, concise piece of factual information from the context.
Your factoid question should be formulated in the same style as questions users could ask in a search engine.
This means that your factoid question MUST NOT mention something like "according to the passage" or "context".

Provide your answer as follows:

------------
{context}
------------

Create 5 Question and Answer pairs in JSON format.
Make sure not to lose any important information.
here is an example:
\"question\": \"What is AI?\", \"answer\": \"AI stands for Artificial Intelligence.\", \
\"question\": \"What is ML?\", \"answer\": \"ML stands for Machine Learning.\", \
"""

In [ ]:
PROMPT_QUESTIONS = PromptTemplate(template=prompt_template, input_variables=["context"])

In [ ]:
# genration part
from langchain_groq import ChatGroq

llm = ChatGroq(
    model="llama3-70b-8192"
)

In [ ]:
from langchain_core.output_parsers import BaseOutputParser
from typing import List, Dict
import re
import json

class dictOutput(BaseOutputParser):
    def parse(self, text: str) -> List[Dict[str, str]]:
        # Finding all JSON objects in the text
        matches = re.findall(r'\{[^}]+\}', text)
        
        if not matches:
            print("No JSON objects found in the input text.")
            return []
        
        result = []
        
        for json_text in matches:
            try:
                # Load the JSON data
                data = json.loads(json_text)
                
                # Extract the question and answer
                question = data.get("question")
                answer = data.get("answer")
                
                if question is not None and answer is not None:
                    result.append({
                        "question": question,
                        "answer": answer
                    })
                else:
                    print(f"Invalid JSON object found: missing 'question' or 'answer' key in {json_text}")
            except json.JSONDecodeError:
                print(f"Invalid JSON format found in text: {json_text}")
        
        return result


In [ ]:
# Chain for generating question and answer
chain_for_qa = PROMPT_QUESTIONS | llm | dictOutput()

In [ ]:
print(chain_for_qa.invoke(docs[2].page_content))

In [ ]:
import csv
import time


# List to hold all question-answer pairs
qa_pairs_list = []

# Maximum number of requests per minute
max_requests_per_minute = 13
# Time interval between requests in seconds
interval = 60 / max_requests_per_minute

# Loop through each document and process its content
for index, doc in enumerate(docs):
    # Get the page content
    page_content = doc.page_content
    
    # Invoke the chain to get question-answer pairs
    qa_pairs = chain_for_qa.invoke(page_content)
    
    # Assuming the output of `invoke` is a list of question-answer pairs
    qa_pairs_list.extend(qa_pairs)
    
    # Wait to respect the rate limit, except after the last request
    if (index + 1) % max_requests_per_minute == 0:
        print("Reached the limit of 13 requests per minute. Waiting for the next minute...")
        time.sleep(60)  # Wait for a minute before making more requests
    else:
        time.sleep(interval)  # Wait for the calculated interval before the next request

# Define the CSV file name
csv_file_name = 'qa_pairs.csv'

# Save the collected question-answer pairs to a CSV file
with open(csv_file_name, mode='w', newline='', encoding='utf-8') as csv_file:
    fieldnames = ['question', 'answer']
    writer = csv.DictWriter(csv_file, fieldnames=fieldnames)

    writer.writeheader()
    for qa in qa_pairs_list:
        writer.writerow(qa)

print(f"Question-answer pairs have been saved to {csv_file_name}")


loding embeddings

In [5]:
from langchain_community.embeddings import HuggingFaceEmbeddings
def download_hugging_face_embdinds():
    embeddings = HuggingFaceEmbeddings(model_name="sentence-transformers/all-MiniLM-L6-v2")
    return embeddings

embeddings = download_hugging_face_embdinds()


c:\github\openai\athina-ai\env\lib\site-packages\langchain_core\_api\deprecation.py:119: LangChainDeprecationWarning: The class `HuggingFaceEmbeddings` was deprecated in LangChain 0.2.2 and will be removed in 0.3.0. An updated version of the class exists in the langchain-huggingface package and should be used instead. To use it run `pip install -U langchain-huggingface` and import as `from langchain_huggingface import HuggingFaceEmbeddings`.
  warn_deprecated(
c:\github\openai\athina-ai\env\lib\site-packages\sentence_transformers\cross_encoder\CrossEncoder.py:11: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm, trange
c:\github\openai\athina-ai\env\lib\site-packages\huggingface_hub\file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new 

In [6]:
AZURE_OPENAI_API_KEY = os.getenv("AZURE_OPENAI_API_KEY")

os.environ["AZURE_OPENAI_API_KEY"] = AZURE_OPENAI_API_KEY

In [7]:
azure_configs = {
    "base_url": "https://evalragas.openai.azure.com/",
    "model_deployment": "ragaseval",
    "model_name": "gpt-35-turbo-16k",

}

In [8]:
from langchain_openai.chat_models import AzureChatOpenAI
from langchain_openai.embeddings import AzureOpenAIEmbeddings
from ragas import evaluate

azure_model = AzureChatOpenAI(
    openai_api_version="2024-02-01",
    azure_endpoint=azure_configs["base_url"],
    azure_deployment=azure_configs["model_deployment"],
    model=azure_configs["model_name"],
    api_key = AZURE_OPENAI_API_KEY
    # validate_base_url=False,
)

try to genrate data by ragas but not work 

In [27]:
from ragas.testset.generator import TestsetGenerator
from ragas.testset.evolutions import simple, reasoning, multi_context

generator = TestsetGenerator.from_langchain(
    azure_model,
    azure_model,
    embeddings
)
testset = generator.generate_with_langchain_docs(docs, test_size=30, distributions={simple: 0.5, reasoning: 0.25, multi_context: 0.25})

embedding nodes:   0%|          | 0/88 [00:00<?, ?it/s]

Filename and doc_id are the same for all nodes.


Generating:   0%|          | 0/31 [00:00<?, ?it/s]

max retries exceeded for SimpleEvolution(generator_llm=LangchainLLMWrapper(run_config=RunConfig(timeout=60, max_retries=15, max_wait=90, max_workers=16, exception_types=(<class 'Exception'>,), log_tenacity=False)), docstore=InMemoryDocumentStore(splitter=<langchain_text_splitters.base.TokenTextSplitter object at 0x000001C69647AC50>, nodes=[Node(page_content='Your car insurance \npolicy booklet', metadata={'source': 'C:\\github\\openai\\athina-ai\\data\\policy-booklet-0923.pdf', 'page': 0}, doc_id='2a6be6bf-cd5b-4a43-9330-8405939c4395', wins=2), Node(page_content='Page 2FAQs  3\nGlossary  4\nMaking a claim  6\nWhat your cover includes  8\nSection 1: Liability  11\nSection 2: Fire and theft  14\nSection 3: Courtesy car  17\nSection 4: Accidental damage  18\nSection 5: Windscreen damage  20\nSection 6: Personal benefits  21\nSection 7: Motor Legal Cover  23\nSection 8: Guaranteed Hire Car Plus  28\nSection 9: Protected No Claim Discount  30Where you can drive  31\nLosses we don’t cover  3

In [28]:
testset.to_pandas()

question  \
0   What steps can you take if you are unhappy wit...   
1   What are the criteria for a car to be consider...   
2   What happens if your appointed representative ...   
3   What does the insurance cover in terms of repa...   
4   What is the purpose of paying an additional pr...   
5   What are the cover amounts shown in 'What your...   
6   What is the significance of using an approved ...   
7   What is the definition of an automated car acc...   
8   How is the renewal premium adjusted based on t...   
9   What does the liability cover for automated ca...   
10  What happens to the No Claim Discount if you m...   
11  What does the comprehensive coverage include i...   
12  What are the criteria for a car to be consider...   
13  What options are available for repairing or re...   
14  What does the coverage include for replacing o...   
15  What information does the Acknowledgement comm...   
16  What is the optional extra for Third Party, Fi...   
17  Who provides the hire car in the Guaranteed Hi...   
18  What exclusions are listed in the liability se...   

                                             contexts  \
0   [Independent review\nIf we don’t complete our ...   
1   [Page 28About Guaranteed Hire Car Plus\nWe’ll ...   
2   [Settling or ending your claim\nOffers to sett...   
3   [Windscreen damage\nWe’ll help put things righ...   
4   [Page 30\nAbout Protected No Claim Discount\nT...   
5   [Windscreen damage\nWe’ll help put things righ...   
6   [Page 7Making a claim\nHow repairs and replace...   
7   [Page 4About the glossary\nWhen we use these w...   
8   [premium, unless there has been any fraudulent...   
9   [Page 13Section 1: Liability\nLiability for au...   
10  [Page 30\nAbout Protected No Claim Discount\nT...   
11  [Page 9What your cover includes\nThird Party, ...   
12  [Page 28About Guaranteed Hire Car Plus\nWe’ll ...   
13  [Page 18Damage to your car\nWe’ll put things r...   
14  [Windscreen damage\nWe’ll help put things righ...   
15  [Page 42If you have a complaint\nHow we can he...   
16  [Page 23Section 7: Motor Legal Cover\nAbout Mo...   
17  [Page 28About Guaranteed Hire Car Plus\nWe’ll ...   
18  [Page 14You’re not covered under this \nsub-se...   

                                         ground_truth evolution_type  \
0   If you are unhappy with the response to your c...         simple   
1   If you have an accident or need to claim, your...         simple   
2   If your appointed representative refuses to co...         simple   
3   The insurance covers the repair of any scratch...         simple   
4   The purpose of paying an additional premium in...         simple   
5                                                 nan         simple   
6   If our approved repairer carries out the repai...         simple   
7   Your car where it is lawfully driving itself o...         simple   
8   If you don’t claim on your policy, the renewal...         simple   
9   The liability cover for automated cars in Grea...         simple   
10  The NCD owner will keep their No Claim Discoun...         simple   
11  The comprehensive coverage includes accidental...         simple   
12  If you have an accident or need to claim, your...         simple   
13  If your car is accidentally damaged, you have ...         simple   
14  The coverage includes replacing or repairing b...         simple   
15  The Acknowledgement communication provides inf...      reasoning   
16  Motor Legal Cover is an optional extra for Thi...      reasoning   
17  The hire car in the Guaranteed Hire Car Plus p...  multi_context   
18  The exclusions listed in the liability section...  multi_context   

                                             metadata  episode_done  
0   [{'source': 'C:\github\openai\athina-ai\data\p...          True  
1   [{'source': 'C:\github\openai\athina-ai\data\p...          True  
2   [{'source': 'C:\github\openai\athina-ai\data\p...          True  
3   [{'source': 'C:\github\openai\athina-a

In [10]:
import pandas as pd
df = pd.read_csv("qa_pairs1.csv")

In [11]:
df.rename(columns={"answer": "ground_truth"}, inplace=True)

In [12]:
df = df.sample(n=50).reset_index(drop=True)

In [13]:
df


question  \
0   What happens if your appointed representative ...   
1   What information do I need to have ready when ...   
2            What is a courtesy car in car insurance?   
3   What should you do if you are in an accident a...   
4                             Who is the main driver?   
5   How long can I have a car for if I use a diffe...   
6   What happens if the policyholder is found lega...   
7   What is not covered if someone takes my car by...   
8          What is an automated car in car insurance?   
9   How many claims are allowed in 3 years with Pr...   
10  What is not covered when driving on a specific...   
11  What type of insurance policies include cover ...   
12      What is not covered in case of a cyber event?   
13  What happens if you cancel your Direct Debit p...   
14  What changes can be made to a car insurance po...   
15  What is the limit of hotel expenses coverage p...   
16       What happens to my car if it is written off?   
17  What happens if I arrange windscreen repairs o...   
18  What type of policies include windscreen damag...   
19  What is required to add Foreign Use Extension ...   
20           What is covered under windscreen damage?   
21  What is included in 'Costs' under Motor Legal ...   
22   Why is a car insurance policy booklet important?   
23  What is not covered if caused by a failure to ...   
24  What is the maximum amount covered for persona...   
25  Are child car seats covered in case of an acci...   
26    What is not covered in case of electronic data?   
27  What is the maximum number of days of car insu...   
28  What is not covered by Motor Legal Cover in ca...   
29           What is not covered in the event of war?   
30  Is a courtesy car included with Comprehensive ...   
31  How much notice will you receive if we need to...   
32  What does a car insurance policy booklet contain?   
33                                 What is DriveSure?   
34  What is the total travel cost limit with Guara...   
35  What is the phone number to call from the UK t...   
36  What is the maximum amount I can claim for per...   
37                 Where must your car be registered?   
38  Under what circumstances will the insurer prov...   
39  What is the limit for removable electronic equ...   
40        What is not covered in case of an accident?   
41  What must you do to ensure your car is protected?   
42  What type of insurance policies can you add Pr...   
43  How many sections are there in the policy book...   
44      What is covered under customs duty in Europe?   
45  What happens if my car is damaged and I have a...   
46  What should I do if I receive any communicatio...   
47  What happens if you don't provide correct and ...   
48                Who regulates UK Insurance Limited?   
49  What is covered in case of emergency medical t...   

                                         ground_truth  
0   The insurer will end cover for your costs imme...  
1   Personal details, policy number, car registrat...  
2   A small hatchback car, or similar car, that an...  
3   Take photos of the accident, including any veh...  
4   The person you declared was the main user of y...  
5                                             21 days  
6   The insurance company will cover the policyhol...  
7   Loss or damage to your car if someone takes it...  
8   A car that is lawfully driving itself on roads...  
9                                            2 claims  
10  Any loss, damage, liability or injury on the N...  
11      Essentials, Comprehensive, Comprehensive Plus  
12    Loss, damage, legal liability, cost or expense.  
13  It won’t cancel the policy, and you’ll be aske...  
14  Temporary or permanent changes can be made to ...  
15       The total we’ll pay for everyone in your car  
16  It becomes our property and you must send us t...  
17  You don’t need to get approval beforehand, but...  
18      Essentials, Comprehensive, Comprehensive Plus  
19  Pay extra and

In [14]:
questions = df["question"].to_list()

ground_truth = df["ground_truth"].to_list()

In [15]:
len(questions)

50

loading orignal RAG model 

In [16]:
from langchain.vectorstores import pinecone
from langchain.schema.runnable import RunnablePassthrough
from langchain.schema.output_parser import StrOutputParser
from langchain.retrievers import ContextualCompressionRetriever
from langchain_cohere import CohereRerank
from langchain_pinecone import PineconeVectorStore

In [17]:
index_name = "policybot"
# Connect to Pinecone index 
vectorstore = PineconeVectorStore(index_name=index_name, embedding=embeddings)
# genration part
from langchain_groq import ChatGroq

llm = ChatGroq(
    model="llama3-70b-8192"
)
prompt_template="""
You are an a professional AI assistant for car insurance inquiries, \
use the provided information to accurately address the user's question. \
If the answer is not available, clearly state that you do not have the information instead of providing a speculative response.
-----------------------------
Context: {context}
-----------------------------
Question: {question}

Please provide in professional and helpful answer below , without any additional commentary.
Helpful answer:
"""
PROMPT=PromptTemplate(template=prompt_template, input_variables=["context", "question"])
parser = StrOutputParser()
compressor = CohereRerank(cohere_api_key="nbDqU1hTVxWmXGbLYI6OnYhp4Cx40MZ5hOmO5oKX")
compression_retriever = ContextualCompressionRetriever(
    base_compressor=compressor, base_retriever=vectorstore.as_retriever(search_kwargs={"k": 5})
    )
chain = (
    {
        "context":  compression_retriever,
        "question":  RunnablePassthrough(),
    }
    | PROMPT
    | llm
    | parser
)

genrating data form model

In [18]:
from datasets import Dataset

data = {"question": [], "answer": [], "contexts": [], "ground_truth": ground_truth}

for query in questions:
    data["question"].append(query)
    data["answer"].append(chain.invoke(query))
    data["contexts"].append([doc.page_content for doc in compression_retriever.invoke(query)])

dataset = Dataset.from_dict(data)

In [19]:
dataset.to_csv("final_data.csv")

Creating CSV from Arrow format:   0%|          | 0/1 [00:00<?, ?ba/s]

146061

evaluation metrics

In [20]:
from ragas.metrics import (
    context_precision,
    answer_relevancy,
    faithfulness,
    context_recall,
)
from ragas.metrics.critique import harmfulness

# list of metrics we're going to use
metrics = [
    faithfulness,
    answer_relevancy,
    context_recall,
    context_precision,
    harmfulness,
]

In [21]:
from ragas.llms import LangchainLLMWrapper
# wrapper around azure_model
ragas_azure_model = LangchainLLMWrapper(azure_model)
# patch the new RagasLLM instance
answer_relevancy.llm = ragas_azure_model
for m in metrics:
    m.__setattr__("llm", ragas_azure_model)

In [22]:

from ragas import evaluate

result = evaluate(
        dataset,
        metrics=[
            context_precision,
            faithfulness,
            answer_relevancy,
            context_recall,
            harmfulness
        ],
        llm=azure_model, embeddings=embeddings
    )

result

Evaluating:   0%|          | 0/250 [00:00<?, ?it/s]

{'context_precision': 0.9083, 'faithfulness': 0.8132, 'answer_relevancy': 0.8513, 'context_recall': 0.9389, 'harmfulness': 0.0000}

In [23]:
result.to_pandas()

question  \
0   What happens if your appointed representative ...   
1   What information do I need to have ready when ...   
2            What is a courtesy car in car insurance?   
3   What should you do if you are in an accident a...   
4                             Who is the main driver?   
5   How long can I have a car for if I use a diffe...   
6   What happens if the policyholder is found lega...   
7   What is not covered if someone takes my car by...   
8          What is an automated car in car insurance?   
9   How many claims are allowed in 3 years with Pr...   
10  What is not covered when driving on a specific...   
11  What type of insurance policies include cover ...   
12      What is not covered in case of a cyber event?   
13  What happens if you cancel your Direct Debit p...   
14  What changes can be made to a car insurance po...   
15  What is the limit of hotel expenses coverage p...   
16       What happens to my car if it is written off?   
17  What happens if I arrange windscreen repairs o...   
18  What type of policies include windscreen damag...   
19  What is required to add Foreign Use Extension ...   
20           What is covered under windscreen damage?   
21  What is included in 'Costs' under Motor Legal ...   
22   Why is a car insurance policy booklet important?   
23  What is not covered if caused by a failure to ...   
24  What is the maximum amount covered for persona...   
25  Are child car seats covered in case of an acci...   
26    What is not covered in case of electronic data?   
27  What is the maximum number of days of car insu...   
28  What is not covered by Motor Legal Cover in ca...   
29           What is not covered in the event of war?   
30  Is a courtesy car included with Comprehensive ...   
31  How much notice will you receive if we need to...   
32  What does a car insurance policy booklet contain?   
33                                 What is DriveSure?   
34  What is the total travel cost limit with Guara...   
35  What is the phone number to call from the UK t...   
36  What is the maximum amount I can claim for per...   
37                 Where must your car be registered?   
38  Under what circumstances will the insurer prov...   
39  What is the limit for removable electronic equ...   
40        What is not covered in case of an accident?   
41  What must you do to ensure your car is protected?   
42  What type of insurance policies can you add Pr...   
43  How many sections are there in the policy book...   
44      What is covered under customs duty in Europe?   
45  What happens if my car is damaged and I have a...   
46  What should I do if I receive any communicatio...   
47  What happens if you don't provide correct and ...   
48                Who regulates UK Insurance Limited?   
49  What is covered in case of emergency medical t...   

                                               answer  \
0   If your appointed representative stops acting ...   
1   When making a claim, you'll need to have the f...   
2   A courtesy car is a small hatchback car, with ...   
3   If you're in an accident and it's safe to do s...   
4   The policy does not explicitly define who the ...   
5   If your car can be repaired and is driveable, ...   
6   If the policyholder is found legally responsib...   
7   We won't cover loss or damage to your car if s...   
8   According to the provided policy booklet, an a...   
9   With Protected No Claim Discount, you are allo...   
10  According to the policy, we won't cover any lo...   
11  The insurance policies that include cover for ...   
12  According to the policy, losses caused by a cy...   
13  If you cancel your Direct Debit payments, it w...   
14  You can make temporary or permanent changes to...   
15  The policy does not specify a specific limit f...   
16  If your car is written off, we will settle you...   
17  You don't need to get our approval beforehand,...   
18  Windscreen damage cover is included with the f... 

In [26]:
df = result.to_pandas()
df.to_excel("final_ragas_evaluation_results.xlsx")

In [33]:
import seaborn as sns
import matplotlib.pyplot as plt
from matplotlib.colors import LinearSegmentedColormap

# Select relevant columns for the heatmap
heatmap_data = df[['harmfulness', 'context_precision', 'context_recall', 'faithfulness', 'answer_relevancy']]

# Define a custom colormap
cmap = LinearSegmentedColormap.from_list('green_red', ['red', 'green'])

plt.figure(figsize=(10, 8))
sns.heatmap(heatmap_data, annot=True, fmt='.2f', linewidths=.5, cmap=cmap)

plt.yticks(ticks=range(len(df['question'])), labels=df['question'], rotation=0)

plt.show()